# Welcome to where to live on Mars's program !! 

Here you can define the best place for you to live on Mars by specifying some parameters. 
There is a few things you have to know about the parameters before you start : 

- relief parameter :  
    The relief parameter ranges between 0 degrees and 90 degrees, so please choose an angle range between these two values.
    
    
- temperature parameter : 
    On Mars, it's quite freezing !! Temperature ranges between approximately  -128 celsius degrees and 12 celsius degrees on its 
    surface, so be sure to choose a temperature range between these two values.
    
    
- ice consistency parameter :
    The ice consistency ranges between -1 and 1. It shows where you will most likely find ice water
    under the surface of Mars. The -1 value means that there is most likely no ice under the surface of this area, and  
    means that there is most likely ice there. Be sure you choose a ice consistency range between these values.
      
      
      
- luminosity parameter : This parameter shows the value of the sun angle on Mars. It ranges between 0 degrees and 90 degrees. You may want to have as much sun as you can have (the bigger the angle, the brightest it will be)


You can choose any values you want but in order to have as much possibility as possible, it is better if your values fit in the ranges described above. 

# Now it's all up to you ! Have fun ! :)

In [14]:
import arcpy
arcpy.env.workspace = "C:/MARS_PROJECT"
print(arcpy.Exists(arcpy.env.workspace))
print(arcpy.CheckOutExtension("Spatial"))
arcpy.env.overwriteOutput = True

#ALREADY EXISTS
#root = "C:/MARS_PROJECT"
#rgdb = "MARSANALYSIS.gdb"
#raster_gdb = root + "/" + rgdb

#if arcpy.Exists(raster_gdb):
   # arcpy.Delete_management(raster_gdb)
   # print("Deleting", raster_gdb)
#else:
   # print("Creating", raster_gdb)
   # arcpy.CreateFileGDB_management(root, rgdb)

True
CheckedOut


In [15]:
import marstime
import arcpy


def create_maxsolarangle():
    feature_class = "C:/project/Vectors.gdb/marsfishnet_label"
    fields = ['sunangle','POINT_X','POINT_Y']
    with arcpy.da.UpdateCursor(feature_class,fields) as cursor:
        for row in cursor:
            solarangle = marstime.solar_elevation(row[1],row[2])
            #row[2]= marstime.solar_elevation(row[1][0],row[1][1])
            #print(row[0],row[1])
            row[0]=solarangle
            cursor.updateRow(row)
            print(row)

    def zerolistmaker(n):
        listofzeros = [0] * n
        return listofzeros

    fields = ['sunangle','POINT_X','POINT_Y']

    max_angle_during_dayN = zerolistmaker(90)
    max_angle_during_dayS = zerolistmaker(90)
    # There are minus latitudes
    with arcpy.da.SearchCursor(feature_class,fields) as cursor:
        for row in cursor:
            # print(row[0],row[1], int(row[2]))
            if(row[2]>=0):
                if(row[0] > max_angle_during_dayN[int(row[2])]):
                    max_angle_during_dayN[int(row[2])] = row[0]
            else:
                if(row[0] > max_angle_during_dayS[int(row[2])*-1]):
                    max_angle_during_dayS[int(row[2])*-1] = row[0]  
    fields = arcpy.ListFields(feature_class)
    field_names = []
    for field in fields:
        field_names.append(field.name)
    if "maxsolarangle" not in fields:
        arcpy.AddField_management(feature_class,"maxsolarangle", "FLOAT")
    fields = arcpy.ListFields(feature_class)
    field_names = []
    for field in fields:
        field_names.append(field.name)
    fields = ['POINT_X', 'POINT_Y', 'maxsolarangle']

    with arcpy.da.UpdateCursor(feature_class,fields) as cursor:
        for row in cursor:
            # print(row)
            if (row[1]>=0):
                row[2] = max_angle_during_dayN[int(row[1])]
            else:
                row[2] = max_angle_during_dayS[-1 * int(row[1])]
            cursor.updateRow(row)
    del cursor
    valField = "maxsolarangle"
    outRaster = "C:/MARS_PROJECT/MARSANALYSIS.gdb/maxsolarangle"
    assignmentType = "MAXIMUM"
    priorityField = ""
    cellSize = 1

    # Execute PointToRaster
    arcpy.arcpy.conversion.PointToRaster(feature_class, valField, outRaster, 
                                         assignmentType, priorityField, cellSize)

In [16]:
import arcpy
from arcpy import env
from arcpy.sa import *
def choose_where_to_live_on_Mars(max_relief_angle,min_relief_angle,max_temp,min_temp,max_ice_consistency,min_ice_consistency,max_sun_angle,min_sun_angle):

    temp_map = arcpy.env.workspace + '/temp_surf'
    Ice_presence = arcpy.env.workspace + "/ice_con"
    #Create the sun angle map based of the day's data the user runs the function
    create_maxsolarangle()
    Luminosity_intensity = "C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/maxsolarangle"
    
    #Get the slope from the relief map
    slope_Mars = arcpy.sa.Slope("/Mars_MGS_MOLA_DEM_mosaic_global_463m.tif", "DEGREE",1)
    slope_Mars_name = "C:/MARS_PROJECT/MARSANALYSIS.gdb/Slope_Mars"
    slope_Mars.save(slope_Mars_name)
    
     # Programm to get the relief area chosen by the user
    slope_Mars_customized1 = arcpy.sa.Con(slope_Mars, slope_Mars,"", "VALUE<=" + str(max_relief_angle))
    slope_Mars_customized = arcpy.sa.Con(slope_Mars_customized1, slope_Mars_customized1,"", "VALUE>=" + str(min_relief_angle))
    #slope_Mars_customized.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/Slope_Mars_custom")
    slope_Mars_custom_norm = (slope_Mars_customized - slope_Mars_customized.minimum)/ (slope_Mars_customized.maximum - slope_Mars_customized.minimum)*100
    slope_Mars_custom_norm1= (slope_Mars_custom_norm - slope_Mars_custom_norm.maximum)* -1
    slope_Mars_custom_norm1.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_relief_area_normalized")
    
     # Programm to get the temperature range area chosen by the user
    temp_map_custom = arcpy.sa.Con(temp_map, temp_map,"", "VALUE<=" + str(max_temp + 273.15))
    temp_map_custom1 = arcpy.sa.Con(temp_map_custom, temp_map_custom,"", "VALUE>=" + str(min_temp + 273.15))
    #temp_map_custom1.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_temp_map")
    temp_map_custom_norm = (temp_map_custom1 - temp_map_custom1.minimum) / (temp_map_custom1.maximum - temp_map_custom1.minimum)*100   
    temp_map_custom_norm.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_temp_area_normalized")
    
     # Programm to get the ice_presence area chosen by the user
    Ice_presence_custom = arcpy.sa.Con(Ice_presence,Ice_presence,"", "VALUE<=" + str(max_ice_consistency))
    Ice_presence_custom1 = arcpy.sa.Con( Ice_presence_custom, Ice_presence_custom,"", "VALUE>=" + str(min_ice_consistency))
    #Ice_presence_custom1.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_ice_presence_area")
    Ice_presence_custom_norm = (Ice_presence_custom1 - Ice_presence_custom1.minimum)/ (Ice_presence_custom1.maximum - Ice_presence_custom1.minimum)*100   
    Ice_presence_custom_norm.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_ice_presence_area_normalized")
    
    # Programm to get the luminosity area chosen by the user
    Luminosity_intensity_custom = arcpy.sa.Con(Luminosity_intensity,Luminosity_intensity,"", "VALUE<=" + str(max_sun_angle))
    Luminosity_intensity_custom1 = arcpy.sa.Con(Luminosity_intensity_custom, Luminosity_intensity_custom,"","VALUE>=" + str(min_sun_angle))
    #Luminosity_intensity_custom1.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_luminosity_area")
    Luminosity_intensity_custom_norm = (Luminosity_intensity_custom1 - Luminosity_intensity_custom1.minimum)/ (Luminosity_intensity_custom1.maximum - Luminosity_intensity_custom1.minimum)*100   
    Luminosity_intensity_custom_norm.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/chosen_luminosity_area_normalized")
    
    
    # Get a union of all the raster layers to get the eligibles areas to live on Mars
    
    eligible_areas = CellStatistics([Raster(slope_Mars_custom_norm1),Raster(Ice_presence_custom_norm),
    Raster(Luminosity_intensity_custom_norm),Raster(temp_map_custom_norm)],"SUM","NODATA","SINGLE_BAND")
    eligible_areas.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/eligible_areas")

choose_where_to_live_on_Mars(12,0,40,-20,0.8,0,90,50)

[17.518465431638475, -0.0016124759999343041, -0.0008039919999305312]
[-7.754659301769692, -178.49999999999997, -89.49999999999994]
[-7.746254870226949, -177.49999999999997, -89.49999999999994]
[-7.737810756012038, -176.49999999999997, -89.49999999999994]
[-7.729329459959743, -175.49999999999997, -89.49999999999994]
[-7.72081363977324, -174.49999999999997, -89.49999999999994]
[-7.712265820218761, -173.49999999999997, -89.49999999999994]
[-7.70368864217852, -172.49999999999997, -89.49999999999994]
[-7.695084757286338, -171.49999999999997, -89.49999999999994]
[-7.686456712969218, -170.49999999999997, -89.49999999999994]
[-7.677807175934461, -169.49999999999997, -89.49999999999994]
[-7.669138781950096, -168.49999999999997, -89.49999999999994]
[-7.660454210104405, -167.49999999999997, -89.49999999999994]
[-7.651756031100277, -166.49999999999997, -89.49999999999994]
[-7.6430469327132045, -165.49999999999997, -89.49999999999994]
[-7.634329606060049, -164.49999999999997, -89.49999999999994]
[-

[-9.040478882684127, 89.50000000000006, -88.49999999999994]
[-9.048457239235134, 90.50000000000006, -88.49999999999994]
[-9.05599771201463, 91.50000000000006, -88.49999999999994]
[-9.063097945466012, 92.50000000000006, -88.49999999999994]
[-9.069755727696347, 93.50000000000006, -88.49999999999994]
[-9.075969053932127, 94.50000000000006, -88.49999999999994]
[-9.081735983686784, 95.50000000000006, -88.49999999999994]
[-9.087054738776772, 96.50000000000006, -88.49999999999994]
[-9.091923662455443, 97.50000000000006, -88.49999999999994]
[-9.096341288414521, 98.50000000000006, -88.49999999999994]
[-9.100306235801241, 99.50000000000006, -88.49999999999994]
[-9.103817281804751, 100.50000000000006, -88.49999999999994]
[-9.106873343556714, 101.50000000000006, -88.49999999999994]
[-9.109473471067375, 102.50000000000006, -88.49999999999994]
[-9.111616879050601, 103.50000000000006, -88.49999999999994]
[-9.113302897104731, 104.50000000000006, -88.49999999999994]
[-9.114531005174314, 105.50000000000

[-4.342636093260026, -51.49999999999994, -86.49999999999994]
[-4.364699991807086, -50.49999999999994, -86.49999999999994]
[-4.3877477347971165, -49.49999999999994, -86.49999999999994]
[-4.411772579474828, -48.49999999999994, -86.49999999999994]
[-4.436767216311765, -47.49999999999994, -86.49999999999994]
[-4.462724134274154, -46.49999999999994, -86.49999999999994]
[-4.489635533322129, -45.49999999999994, -86.49999999999994]
[-4.5174932134454195, -44.49999999999994, -86.49999999999994]
[-4.546289026539412, -43.49999999999994, -86.49999999999994]
[-4.57601421050623, -42.49999999999994, -86.49999999999994]
[-4.606659708969715, -41.49999999999994, -86.49999999999994]
[-4.638216559324576, -40.49999999999994, -86.49999999999994]
[-4.670675158821041, -39.49999999999994, -86.49999999999994]
[-4.704025754765439, -38.49999999999994, -86.49999999999994]
[-4.738258187466499, -37.49999999999994, -86.49999999999994]
[-4.773362445969028, -36.49999999999994, -86.49999999999994]
[-4.809327847344463, -3

[-10.903760080440875, 150.5000000000001, -85.49999999999994]
[-10.849431233999653, 151.5000000000001, -85.49999999999994]
[-10.794115557868494, 152.5000000000001, -85.49999999999994]
[-10.737829935866557, 153.5000000000001, -85.49999999999994]
[-10.68059222319755, 154.5000000000001, -85.49999999999994]
[-10.62242033239177, 155.5000000000001, -85.49999999999994]
[-10.563332698289983, 156.5000000000001, -85.49999999999994]
[-10.503347294598896, 157.5000000000001, -85.49999999999994]
[-10.44248308785113, 158.5000000000001, -85.49999999999994]
[-10.380759061241974, 159.5000000000001, -85.49999999999994]
[-10.318194449705587, 160.5000000000001, -85.49999999999994]
[-10.254808995979516, 161.5000000000001, -85.49999999999994]
[-10.19062189712686, 162.5000000000001, -85.49999999999994]
[-10.125653363458241, 163.5000000000001, -85.49999999999994]
[-10.059923571585259, 164.5000000000001, -85.49999999999994]
[-9.993453191961663, 165.5000000000001, -85.49999999999994]
[-9.92626228521658, 166.50000

[-9.338191802893164, 33.50000000000006, -83.49999999999994]
[-9.447337587432713, 34.50000000000006, -83.49999999999994]
[-9.555943821582858, 35.50000000000006, -83.49999999999994]
[-9.663976401772985, 36.50000000000006, -83.49999999999994]
[-9.771403116474843, 37.50000000000006, -83.49999999999994]
[-9.878190580449072, 38.50000000000006, -83.49999999999994]
[-9.984306001255973, 39.50000000000006, -83.49999999999994]
[-10.089716749414606, 40.50000000000006, -83.49999999999994]
[-10.194389945041308, 41.50000000000006, -83.49999999999994]
[-10.298294164140287, 42.50000000000006, -83.49999999999994]
[-10.40139689939815, 43.50000000000006, -83.49999999999994]
[-10.503665859754406, 44.50000000000006, -83.49999999999994]
[-10.605070209352704, 45.50000000000006, -83.49999999999994]
[-10.705578089412725, 46.50000000000006, -83.49999999999994]
[-10.805158290503343, 47.50000000000006, -83.49999999999994]
[-10.903779447760456, 48.50000000000006, -83.49999999999994]
[-11.001411649009327, 49.5000000

...

[10.692698809261316, -137.49999999999994, 82.50000000000006]
[10.811809954059243, -136.49999999999994, 82.50000000000006]
[10.929969128965965, -135.49999999999994, 82.50000000000006]
[11.047140651516088, -134.49999999999994, 82.50000000000006]
[11.163287639530552, -133.49999999999994, 82.50000000000006]
[11.278373946257446, -132.49999999999994, 82.50000000000006]
[11.39236369023574, -131.49999999999994, 82.50000000000006]
[11.505220811557948, -130.49999999999994, 82.50000000000006]
[11.616910910387375, -129.49999999999994, 82.50000000000006]
[11.727398511573398, -128.49999999999994, 82.50000000000006]
[11.836648912621797, -127.49999999999994, 82.50000000000006]
[11.944627299743104, -126.49999999999994, 82.50000000000006]
[12.051300507874188, -125.49999999999994, 82.50000000000006]
[12.156634402498483, -124.49999999999994, 82.50000000000006]
[12.260595650222314, -123.49999999999994, 82.50000000000006]
[12.363150876524386, -122.49999999999994, 82.50000000000006]
[12.464268336762572, -121

[1.4051929739300135, 90.50000000000006, 83.50000000000006]
[1.372830783731004, 91.50000000000006, 83.50000000000006]
[1.3423493833419258, 92.50000000000006, 83.50000000000006]
[1.313758226283312, 93.50000000000006, 83.50000000000006]
[1.2870657205083376, 94.50000000000006, 83.50000000000006]
[1.262280048466451, 95.50000000000006, 83.50000000000006]
[1.2394087002697347, 96.50000000000006, 83.50000000000006]
[1.2184585889294794, 97.50000000000006, 83.50000000000006]
[1.199436126940526, 98.50000000000006, 83.50000000000006]
[1.1823468998274933, 99.50000000000006, 83.50000000000006]
[1.1671961627772731, 100.50000000000006, 83.50000000000006]
[1.1539884981973785, 101.50000000000006, 83.50000000000006]
[1.1427279437237274, 102.50000000000006, 83.50000000000006]
[1.1334178134705581, 103.50000000000006, 83.50000000000006]
[1.1260609742821828, 104.50000000000006, 83.50000000000006]
[1.1206596521442123, 105.50000000000006, 83.50000000000006]
[1.1172154937864889, 106.50000000000006, 83.5000000000

[11.761638710007105, -49.49999999999994, 85.50000000000006]
[11.730296485456435, -48.49999999999994, 85.50000000000006]
[11.69768906460061, -47.49999999999994, 85.50000000000006]
[11.663826958379502, -46.49999999999994, 85.50000000000006]
[11.628720646744938, -45.49999999999994, 85.50000000000006]
[11.592381417279341, -44.49999999999994, 85.50000000000006]
[11.554820804314076, -43.49999999999994, 85.50000000000006]
[11.516050885393753, -42.49999999999994, 85.50000000000006]
[11.476083630025698, -41.49999999999994, 85.50000000000006]
[11.434931857943141, -40.49999999999994, 85.50000000000006]
[11.392608597432115, -39.49999999999994, 85.50000000000006]
[11.34912723851356, -38.49999999999994, 85.50000000000006]
[11.304501714519716, -37.49999999999994, 85.50000000000006]
[11.258745755584272, -36.49999999999994, 85.50000000000006]
[11.21187398875955, -35.49999999999994, 85.50000000000006]
[11.163901200569654, -34.49999999999994, 85.50000000000006]
[11.114842709928311, -33.49999999999994, 85

[9.548183061030699, -111.49999999999994, 87.50000000000006]
[9.575631639455082, -110.49999999999994, 87.50000000000006]
[9.602481414486931, -109.49999999999994, 87.50000000000006]
[9.628724293350388, -108.49999999999994, 87.50000000000006]
[9.654352032604336, -107.49999999999994, 87.50000000000006]
[9.679356689803086, -106.49999999999994, 87.50000000000006]
[9.703730513245603, -105.49999999999994, 87.50000000000006]
[9.727465855034154, -104.49999999999994, 87.50000000000006]
[9.750555534153818, -103.49999999999994, 87.50000000000006]
[9.772992294271631, -102.49999999999994, 87.50000000000006]
[9.794769171723075, -101.49999999999994, 87.50000000000006]
[9.815879323317418, -100.49999999999994, 87.50000000000006]
[9.836316361327121, -99.49999999999994, 87.50000000000006]
[9.856073852465158, -98.49999999999994, 87.50000000000006]
[9.875145658211352, -97.49999999999994, 87.50000000000006]
[9.89352578033943, -96.49999999999994, 87.50000000000006]
[9.911208650978836, -95.49999999999994, 87.50

[6.1584457513833115, 121.50000000000011, 88.50000000000006]
[6.164864626098733, 122.50000000000011, 88.50000000000006]
[6.171724086212876, 123.50000000000011, 88.50000000000006]
[6.179022036387863, 124.50000000000011, 88.50000000000006]
[6.18675624165455, 125.50000000000011, 88.50000000000006]
[6.194924423842238, 126.50000000000011, 88.50000000000006]
[6.203524086712719, 127.50000000000011, 88.50000000000006]
[6.212552631957664, 128.5000000000001, 88.50000000000006]
[6.2220073316013895, 129.5000000000001, 88.50000000000006]
[6.231885291451647, 130.5000000000001, 88.50000000000006]
[6.2421835997503905, 131.5000000000001, 88.50000000000006]
[6.252899108834342, 132.5000000000001, 88.50000000000006]
[6.264028580554452, 133.5000000000001, 88.50000000000006]
[6.2755686058850415, 134.5000000000001, 88.50000000000006]
[6.287515786856304, 135.5000000000001, 88.50000000000006]
[6.299866468688862, 136.5000000000001, 88.50000000000006]
[6.312616918462453, 137.5000000000001, 88.50000000000006]
[6.3

In [7]:
# Get a union of all the maps
slope_Mars_custom_norm1 = "C:/MARS_PROJECT/MARSANALYSIS.gdb/chosen_relief_area_normalized"
Ice_presence_custom_norm = "C:/MARS_PROJECT/MARSANALYSIS.gdb/chosen_ice_presence_area_normalized"
Luminosity_intensity_custom_norm = "C:/MARS_PROJECT/MARSANALYSIS.gdb/chosen_luminosity_area_normalized"
temp_map_custom_norm = "C:/MARS_PROJECT/MARSANALYSIS.gdb/chosen_temp_area_normalized"


In [8]:
import arcpy
from arcpy import env
from arcpy.sa import *
eligible_areas = CellStatistics([Raster(slope_Mars_custom_norm1),Raster(Ice_presence_custom_norm),Raster(Luminosity_intensity_custom_norm),Raster(temp_map_custom_norm)],"SUM","NODATA","SINGLE_BAND")
eligible_areas.save("C:/MARS_PROJECT/MARSANALYSIS.gdb" + "/eligible_areas")